# Tensor Flow Notebook
## W207 Final Project
### T. P. Goter
### July 6, 2019

This workbook is used to create, fit and analyze various neural networks for facial keypoint detection.

In [1]:
# Import needed packages
from __future__ import absolute_import, division, print_function, unicode_literals
import tensorflow as tf
import pandas as pd
import numpy as np
import time
from tensorflow.keras import models, layers, callbacks
from tensorflow.keras import optimizers, metrics
from matplotlib import pyplot as plt
%matplotlib inline

In [2]:
tf.__version__
tf.keras.backend.clear_session()

## Data Loading

- Load in the pickle file that was created as part of the EDA in DataExploration.ipynb. 
- This dataset has the NaNs removed and a few mislabeled images removed as well. 
- As such there is only limited training and development data to use. 
- The image data has already been normalized to [0,1]

In [3]:
# Initialize Random Seed for reproducibility
np.random.seed(13)

# Load the dataframe from the pickle file
df_nostache_nonan = pd.read_pickle("df_nostache_nonan.pkl")

# Grab the last column - that is our image data for X matrix
X = df_nostache_nonan.iloc[:, -1]

# Convert from a series of arrays to an NDarray
X = np.array([x for x in X])

# Grab the keypoints and stick into our y-variable
y = np.array(df_nostache_nonan.iloc[:,:-1])


In [4]:
X

array([[0.5372549 , 0.54117647, 0.5372549 , ..., 0.50980392, 0.43137255,
        0.3372549 ],
       [0.74509804, 0.48235294, 0.57254902, ..., 0.4745098 , 0.45490196,
        0.45098039],
       [0.01960784, 0.00784314, 0.01568627, ..., 0.65490196, 0.64313725,
        0.63921569],
       ...,
       [0.48235294, 0.48627451, 0.48627451, ..., 0.72156863, 0.72156863,
        0.7254902 ],
       [0.77254902, 0.77647059, 0.77647059, ..., 0.00392157, 0.00392157,
        0.00392157],
       [1.        , 1.        , 1.        , ..., 0.80392157, 0.8       ,
        0.77647059]])

## Baseline Neural Net
CNNs are combinations of convolution layers, pooling layers and dropout layers followed by one or two fully connected layers once the number of dimensions has been sufficiently reduced.

1. Let's include just one hidden layer and one output layer
2. The input layer will reduce our flattened 96x96 matrix (i.e., 9216 in length) to a predetermined number of hidden units
3. We will then run sensitivities to # of hidden units, activation, optimizer, and learning rate
4. We will judge our model based on RMSE error and run time.

In [5]:
def base_model(hidden_units=100, activation='relu'):
    base_model = models.Sequential()
    base_model.add(layers.Dense(hidden_units,activation=activation, kernel_initializer='normal',input_shape=[9216]))
    base_model.add(layers.Dense(30, activation='linear'))
    base_model.build()
    print(base_model.summary())
    return base_model
   
class TimeHistory(callbacks.Callback):
    def on_train_begin(self, logs={}):
        self.times = []

    def on_epoch_begin(self, batch, logs={}):
        self.epoch_time_start = time.time()

    def on_epoch_end(self, batch, logs={}):
        self.times.append(time.time() - self.epoch_time_start)

#### Define our optimizers for our initial study

In [6]:
adam = optimizers.Adam(lr=0.001, beta_1=0.9, beta_2=0.999)
sgd = optimizers.SGD(lr=0.01, momentum=0.9, decay=0.0, nesterov=True)
nadam = optimizers.Nadam(lr=0.002, beta_1=0.9, beta_2=0.999, epsilon=None, schedule_decay=0.004)
adagrad = optimizers.Adagrad(lr=0.01, epsilon=None, decay=0.0)

opt_list = {'adam':adam, 'sgd':sgd, 'nadam':nadam, 'adagrad':adagrad}

#### Set up our first DOE

In [24]:
single_layer_base_df = pd.DataFrame()
for hidden_unit in [50, 100, 150, 200]:
    for act in ['relu', 'sigmoid', 'tanh']:
        for opt_name, opt in opt_list.items():
            model = base_model(hidden_units=hidden_unit, activation=act)
            model.compile(optimizer=opt,
                          loss='mean_squared_error',
                          metrics=['mean_squared_error'])
            time_callback = TimeHistory()
            history = model.fit(X, y, epochs=400, validation_split=0.15, callbacks=[time_callback])
            times = time_callback.times

            # Convert to dataframe
            hist = pd.DataFrame(history.history)
            hist['epoch'] = history.epoch
            hist['RMSE'] = np.sqrt(hist.mean_squared_error)
            hist['val_RMSE'] = np.sqrt(hist.val_mean_squared_error)
            hist['times'] = times
            hist['hunits'] = hidden_unit
            hist['activation'] = act
            hist['optimizer'] = opt_name
            hist['lrate'] = opt.get_config()['learning_rate']

            # Keep concatenating to dataframe
            single_layer_base_df = pd.concat([single_layer_base_df,hist])
            
            # Re-pickle after every model to retain progress
            single_layer_base_df.to_pickle("OutputData/single_layer_df.pkl")

            # Save models.
            filename = "base_model_{}_{}_{}".format(hidden_unit, act, opt_name)
            model.save("Models/"+filename+".h5")


Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense (Dense)                (None, 50)                460850    
_________________________________________________________________
dense_1 (Dense)              (None, 30)                1530      
Total params: 462,380
Trainable params: 462,380
Non-trainable params: 0
_________________________________________________________________
None
Train on 1819 samples, validate on 321 samples
Epoch 1/400
1819/1819 [==============================] - 0s 209us/sample - loss: 622.1051 - mean_squared_error: 622.1052 - val_loss: 170.3350 - val_mean_squared_error: 170.3350
Epoch 2/400
1819/1819 [==============================] - 0s 117us/sample - loss: 158.0834 - mean_squared_error: 158.0834 - val_loss: 159.4654 - val_mean_squared_error: 159.4654
Epoch 3/400
1819/1819 [==============================] - 0s 112us/sample - loss: 149.3548 - mean_squared_e

Epoch 44/400
1819/1819 [==============================] - 0s 114us/sample - loss: 47.3832 - mean_squared_error: 47.3832 - val_loss: 64.3656 - val_mean_squared_error: 64.3656
Epoch 45/400
1819/1819 [==============================] - 0s 117us/sample - loss: 47.5131 - mean_squared_error: 47.5131 - val_loss: 72.7369 - val_mean_squared_error: 72.7369
Epoch 46/400
1819/1819 [==============================] - 0s 114us/sample - loss: 47.1205 - mean_squared_error: 47.1205 - val_loss: 67.0384 - val_mean_squared_error: 67.0384
Epoch 47/400
1819/1819 [==============================] - 0s 110us/sample - loss: 43.6165 - mean_squared_error: 43.6165 - val_loss: 62.2391 - val_mean_squared_error: 62.2391
Epoch 48/400
1819/1819 [==============================] - 0s 109us/sample - loss: 43.3244 - mean_squared_error: 43.3244 - val_loss: 63.3165 - val_mean_squared_error: 63.3165
Epoch 49/400
1819/1819 [==============================] - 0s 113us/sample - loss: 42.4549 - mean_squared_error: 42.4549 - val_loss

Epoch 138/400
1819/1819 [==============================] - 0s 116us/sample - loss: 18.3544 - mean_squared_error: 18.3544 - val_loss: 48.5893 - val_mean_squared_error: 48.5893
Epoch 139/400
1819/1819 [==============================] - 0s 114us/sample - loss: 17.9912 - mean_squared_error: 17.9912 - val_loss: 46.5230 - val_mean_squared_error: 46.5230
Epoch 140/400
1819/1819 [==============================] - 0s 116us/sample - loss: 17.9264 - mean_squared_error: 17.9264 - val_loss: 46.7967 - val_mean_squared_error: 46.7967
Epoch 141/400
1819/1819 [==============================] - 0s 115us/sample - loss: 17.3499 - mean_squared_error: 17.3499 - val_loss: 47.3956 - val_mean_squared_error: 47.3956
Epoch 142/400
1819/1819 [==============================] - 0s 119us/sample - loss: 16.8169 - mean_squared_error: 16.8169 - val_loss: 48.4428 - val_mean_squared_error: 48.4428
Epoch 143/400
1819/1819 [==============================] - 0s 116us/sample - loss: 15.7048 - mean_squared_error: 15.7048 - va

Epoch 185/400
1819/1819 [==============================] - 0s 151us/sample - loss: 11.1804 - mean_squared_error: 11.1804 - val_loss: 41.7249 - val_mean_squared_error: 41.7249
Epoch 186/400
1819/1819 [==============================] - 0s 106us/sample - loss: 11.4255 - mean_squared_error: 11.4255 - val_loss: 41.0600 - val_mean_squared_error: 41.0600
Epoch 187/400
1819/1819 [==============================] - 0s 114us/sample - loss: 14.0519 - mean_squared_error: 14.0519 - val_loss: 43.1157 - val_mean_squared_error: 43.1157
Epoch 188/400
1819/1819 [==============================] - 0s 108us/sample - loss: 12.1361 - mean_squared_error: 12.1361 - val_loss: 41.7291 - val_mean_squared_error: 41.7291
Epoch 189/400
1819/1819 [==============================] - 0s 127us/sample - loss: 11.7778 - mean_squared_error: 11.7778 - val_loss: 40.4114 - val_mean_squared_error: 40.4114
Epoch 190/400
1819/1819 [==============================] - 0s 115us/sample - loss: 10.9200 - mean_squared_error: 10.9200 - va

1819/1819 [==============================] - 0s 110us/sample - loss: 8.8975 - mean_squared_error: 8.8975 - val_loss: 37.6499 - val_mean_squared_error: 37.6499
Epoch 233/400
1819/1819 [==============================] - 0s 107us/sample - loss: 8.5490 - mean_squared_error: 8.5490 - val_loss: 36.4052 - val_mean_squared_error: 36.4052
Epoch 234/400
1819/1819 [==============================] - 0s 106us/sample - loss: 9.2134 - mean_squared_error: 9.2134 - val_loss: 36.1434 - val_mean_squared_error: 36.1434
Epoch 235/400
1819/1819 [==============================] - 0s 110us/sample - loss: 8.4173 - mean_squared_error: 8.4173 - val_loss: 36.1434 - val_mean_squared_error: 36.1434
Epoch 236/400
1819/1819 [==============================] - 0s 109us/sample - loss: 8.5347 - mean_squared_error: 8.5347 - val_loss: 39.2840 - val_mean_squared_error: 39.2840
Epoch 237/400
1819/1819 [==============================] - 0s 108us/sample - loss: 8.8233 - mean_squared_error: 8.8233 - val_loss: 46.8170 - val_mean

...

Epoch 203/400
1819/1819 [==============================] - 1s 387us/sample - loss: 9.5394 - mean_squared_error: 9.5394 - val_loss: 9.2552 - val_mean_squared_error: 9.2552
Epoch 204/400
1819/1819 [==============================] - 1s 390us/sample - loss: 9.5023 - mean_squared_error: 9.5023 - val_loss: 9.2227 - val_mean_squared_error: 9.2227
Epoch 205/400
1819/1819 [==============================] - 1s 388us/sample - loss: 9.4749 - mean_squared_error: 9.4749 - val_loss: 9.2038 - val_mean_squared_error: 9.2038
Epoch 206/400
1819/1819 [==============================] - 1s 388us/sample - loss: 9.4597 - mean_squared_error: 9.4597 - val_loss: 9.1752 - val_mean_squared_error: 9.1752
Epoch 207/400
1819/1819 [==============================] - 1s 388us/sample - loss: 9.4238 - mean_squared_error: 9.4238 - val_loss: 9.1598 - val_mean_squared_error: 9.1598
Epoch 208/400
1819/1819 [==============================] - 1s 409us/sample - loss: 9.4129 - mean_squared_error: 9.4129 - val_loss: 9.2845 - val_m

Epoch 251/400
1819/1819 [==============================] - 1s 379us/sample - loss: 8.8852 - mean_squared_error: 8.8852 - val_loss: 8.8288 - val_mean_squared_error: 8.8288
Epoch 252/400
1819/1819 [==============================] - 1s 383us/sample - loss: 8.8868 - mean_squared_error: 8.8868 - val_loss: 8.8069 - val_mean_squared_error: 8.8069
Epoch 253/400
1819/1819 [==============================] - 1s 394us/sample - loss: 8.8615 - mean_squared_error: 8.8615 - val_loss: 8.7796 - val_mean_squared_error: 8.7796
Epoch 254/400
1819/1819 [==============================] - 1s 398us/sample - loss: 8.8615 - mean_squared_error: 8.8615 - val_loss: 8.7709 - val_mean_squared_error: 8.7709
Epoch 255/400
1819/1819 [==============================] - 1s 383us/sample - loss: 8.8465 - mean_squared_error: 8.8465 - val_loss: 8.7574 - val_mean_squared_error: 8.7574
Epoch 256/400
1819/1819 [==============================] - 1s 384us/sample - loss: 8.8554 - mean_squared_error: 8.8554 - val_loss: 8.7772 - val_m

Epoch 299/400
1819/1819 [==============================] - 1s 393us/sample - loss: 8.4075 - mean_squared_error: 8.4075 - val_loss: 8.4786 - val_mean_squared_error: 8.4786
Epoch 300/400
1819/1819 [==============================] - 1s 391us/sample - loss: 8.3870 - mean_squared_error: 8.3870 - val_loss: 8.4242 - val_mean_squared_error: 8.4242
Epoch 301/400
1819/1819 [==============================] - 1s 483us/sample - loss: 8.3597 - mean_squared_error: 8.3597 - val_loss: 8.5282 - val_mean_squared_error: 8.5282
Epoch 302/400
1819/1819 [==============================] - 1s 506us/sample - loss: 8.3607 - mean_squared_error: 8.3607 - val_loss: 8.4488 - val_mean_squared_error: 8.4488
Epoch 303/400
1819/1819 [==============================] - 1s 448us/sample - loss: 8.3627 - mean_squared_error: 8.3627 - val_loss: 8.5018 - val_mean_squared_error: 8.5018
Epoch 304/400
1819/1819 [==============================] - 1s 419us/sample - loss: 8.3370 - mean_squared_error: 8.3370 - val_loss: 8.4142 - val_m

Epoch 347/400
1819/1819 [==============================] - 1s 382us/sample - loss: 7.9500 - mean_squared_error: 7.9500 - val_loss: 8.1206 - val_mean_squared_error: 8.1206
Epoch 348/400
1819/1819 [==============================] - 1s 384us/sample - loss: 7.9205 - mean_squared_error: 7.9205 - val_loss: 8.2190 - val_mean_squared_error: 8.2190
Epoch 349/400
1819/1819 [==============================] - 1s 389us/sample - loss: 7.9132 - mean_squared_error: 7.9132 - val_loss: 8.1141 - val_mean_squared_error: 8.1141
Epoch 350/400
1819/1819 [==============================] - 1s 384us/sample - loss: 7.9048 - mean_squared_error: 7.9048 - val_loss: 8.0981 - val_mean_squared_error: 8.0981
Epoch 351/400
1819/1819 [==============================] - 1s 385us/sample - loss: 7.8924 - mean_squared_error: 7.8924 - val_loss: 8.1053 - val_mean_squared_error: 8.1053
Epoch 352/400
1819/1819 [==============================] - 1s 382us/sample - loss: 7.8669 - mean_squared_error: 7.8669 - val_loss: 8.0774 - val_m

Epoch 395/400
1819/1819 [==============================] - 1s 435us/sample - loss: 7.4547 - mean_squared_error: 7.4547 - val_loss: 7.7482 - val_mean_squared_error: 7.7482
Epoch 396/400
1819/1819 [==============================] - 1s 431us/sample - loss: 7.4474 - mean_squared_error: 7.4474 - val_loss: 7.8015 - val_mean_squared_error: 7.8015
Epoch 397/400
1819/1819 [==============================] - 1s 431us/sample - loss: 7.4326 - mean_squared_error: 7.4326 - val_loss: 7.7669 - val_mean_squared_error: 7.7669
Epoch 398/400
1819/1819 [==============================] - 1s 449us/sample - loss: 7.4093 - mean_squared_error: 7.4093 - val_loss: 7.7324 - val_mean_squared_error: 7.7324
Epoch 399/400
1819/1819 [==============================] - 1s 494us/sample - loss: 7.3954 - mean_squared_error: 7.3954 - val_loss: 7.7605 - val_mean_squared_error: 7.7605
Epoch 400/400
1819/1819 [==============================] - 1s 435us/sample - loss: 7.3924 - mean_squared_error: 7.3924 - val_loss: 7.7605 - val_m

### Learning Rate Experiment - ADAM and SGD
- Let's run two additional learning rates for adam and SGD.
- we will evaluate both with a straight relu activation methodology.

In [5]:
# We already have the default learning rate for adam. So let's move up and down to determine accuracy sensitivity
adam_005 = optimizers.Adam(lr=0.005, beta_1=0.9, beta_2=0.999)
adam_0005 = optimizers.Adam(lr=0.0005, beta_1=0.9, beta_2=0.999)

# We already have the default learning rate for adagrad. So let's move up and down to determine accuracy sensitivity
sgd_05 = optimizers.SGD(lr=0.05, momentum=0.9, decay=0.0, nesterov=True)
sgd_005 = optimizers.Adagrad(lr=0.005, epsilon=None, decay=0.0)

opt_list_lr = {'adam_005':adam_005, 'adam_0005':adam_0005, 'sgd_05':sgd_05, 'sgd_005':sgd_005}

## Run the learning rate experiment
Now that we have our updated optimizers generated. Lets run our experiment.

In [7]:
single_layer_lr_df = pd.DataFrame()
for hidden_unit in [50, 100, 150, 200]:
    for act in ['relu']:
        for opt_name, opt in opt_list.items():
            model = base_model(hidden_units=hidden_unit, activation=act)
            model.compile(optimizer=opt,
                          loss='mean_squared_error',
                          metrics=['mean_squared_error'])
            time_callback = TimeHistory()
            history = model.fit(X, y, epochs=400, validation_split=0.15, callbacks=[time_callback])
            times = time_callback.times

            # Convert to dataframe
            hist = pd.DataFrame(history.history)
            hist['epoch'] = history.epoch
            hist['RMSE'] = np.sqrt(hist.mean_squared_error)
            hist['val_RMSE'] = np.sqrt(hist.val_mean_squared_error)
            hist['times'] = times
            hist['hunits'] = hidden_unit
            hist['activation'] = act
            hist['optimizer'] = opt_name
            hist['lrate'] = opt.get_config()['learning_rate']

            # Keep concatenating to dataframe
            single_layer_lr_df = pd.concat([single_layer_lr_df,hist])
            
            # Re-pickle after every model to retain progress
            single_layer_lr_df.to_pickle("OutputData/single_layer_lr_df.pkl")

            # Save models.
            filename = "base_model_lr_{}_{}_{}".format(hidden_unit, act, opt_name)
            model.save("Models/"+filename+".h5")

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense (Dense)                (None, 50)                460850    
_________________________________________________________________
dense_1 (Dense)              (None, 30)                1530      
Total params: 462,380
Trainable params: 462,380
Non-trainable params: 0
_________________________________________________________________
None
Train on 1819 samples, validate on 321 samples
Epoch 1/400
1819/1819 [==============================] - 1s 486us/sample - loss: 607.3001 - mean_squared_error: 607.3002 - val_loss: 168.9939 - val_mean_squared_error: 168.9938
Epoch 2/400
1819/1819 [==============================] - 0s 114us/sample - loss: 157.7771 - mean_squared_error: 157.7771 - val_loss: 158.7946 - val_mean_squared_error: 158.7946
Epoch 3/400
1819/1819 [==============================] - 0s 113us/sample - loss: 149.4325 - mean_squared_e

Epoch 44/400
1819/1819 [==============================] - 0s 127us/sample - loss: 49.9843 - mean_squared_error: 49.9843 - val_loss: 66.4336 - val_mean_squared_error: 66.4336
Epoch 45/400
1819/1819 [==============================] - 0s 124us/sample - loss: 49.5667 - mean_squared_error: 49.5667 - val_loss: 67.5636 - val_mean_squared_error: 67.5636
Epoch 46/400
1819/1819 [==============================] - 0s 118us/sample - loss: 50.3632 - mean_squared_error: 50.3633 - val_loss: 64.8370 - val_mean_squared_error: 64.8370
Epoch 47/400
1819/1819 [==============================] - 0s 117us/sample - loss: 45.6039 - mean_squared_error: 45.6039 - val_loss: 63.4346 - val_mean_squared_error: 63.4346
Epoch 48/400
1819/1819 [==============================] - 0s 111us/sample - loss: 45.4817 - mean_squared_error: 45.4817 - val_loss: 64.1350 - val_mean_squared_error: 64.1350
Epoch 49/400
1819/1819 [==============================] - 0s 119us/sample - loss: 45.6273 - mean_squared_error: 45.6273 - val_loss

1819/1819 [==============================] - 0s 123us/sample - loss: 32.0494 - mean_squared_error: 32.0494 - val_loss: 52.9597 - val_mean_squared_error: 52.9596
Epoch 92/400
1819/1819 [==============================] - 0s 117us/sample - loss: 27.7827 - mean_squared_error: 27.7827 - val_loss: 51.3676 - val_mean_squared_error: 51.3676
Epoch 93/400
1819/1819 [==============================] - 0s 115us/sample - loss: 26.6124 - mean_squared_error: 26.6124 - val_loss: 52.3426 - val_mean_squared_error: 52.3426
Epoch 94/400
1819/1819 [==============================] - 0s 119us/sample - loss: 26.0847 - mean_squared_error: 26.0847 - val_loss: 54.5905 - val_mean_squared_error: 54.5905
Epoch 95/400
1819/1819 [==============================] - 0s 120us/sample - loss: 25.8123 - mean_squared_error: 25.8123 - val_loss: 53.4230 - val_mean_squared_error: 53.4230
Epoch 96/400
1819/1819 [==============================] - 0s 117us/sample - loss: 25.3996 - mean_squared_error: 25.3996 - val_loss: 52.4678 - v

Epoch 138/400
1819/1819 [==============================] - 0s 123us/sample - loss: 19.6585 - mean_squared_error: 19.6585 - val_loss: 46.5008 - val_mean_squared_error: 46.5008
Epoch 139/400
1819/1819 [==============================] - 0s 121us/sample - loss: 17.2912 - mean_squared_error: 17.2912 - val_loss: 45.4527 - val_mean_squared_error: 45.4527
Epoch 140/400
1819/1819 [==============================] - 0s 125us/sample - loss: 18.0452 - mean_squared_error: 18.0452 - val_loss: 45.5559 - val_mean_squared_error: 45.5559
Epoch 141/400
1819/1819 [==============================] - 0s 111us/sample - loss: 17.7187 - mean_squared_error: 17.7187 - val_loss: 44.7231 - val_mean_squared_error: 44.7231
Epoch 142/400
1819/1819 [==============================] - 0s 104us/sample - loss: 17.4898 - mean_squared_error: 17.4898 - val_loss: 48.0926 - val_mean_squared_error: 48.0926
Epoch 143/400
1819/1819 [==============================] - 0s 102us/sample - loss: 15.9128 - mean_squared_error: 15.9128 - va

Epoch 185/400
1819/1819 [==============================] - 0s 106us/sample - loss: 11.5685 - mean_squared_error: 11.5685 - val_loss: 39.9440 - val_mean_squared_error: 39.9440
Epoch 186/400
1819/1819 [==============================] - 0s 103us/sample - loss: 11.7612 - mean_squared_error: 11.7612 - val_loss: 39.6318 - val_mean_squared_error: 39.6318
Epoch 187/400
1819/1819 [==============================] - 0s 104us/sample - loss: 14.5009 - mean_squared_error: 14.5009 - val_loss: 42.5632 - val_mean_squared_error: 42.5632
Epoch 188/400
1819/1819 [==============================] - 0s 112us/sample - loss: 11.7833 - mean_squared_error: 11.7833 - val_loss: 40.9818 - val_mean_squared_error: 40.9818
Epoch 189/400
1819/1819 [==============================] - 0s 113us/sample - loss: 12.1091 - mean_squared_error: 12.1091 - val_loss: 39.7024 - val_mean_squared_error: 39.7024
Epoch 190/400
1819/1819 [==============================] - 0s 105us/sample - loss: 11.7380 - mean_squared_error: 11.7380 - va

...

Epoch 193/400
1819/1819 [==============================] - 1s 381us/sample - loss: 22.2343 - mean_squared_error: 22.2343 - val_loss: 48.6438 - val_mean_squared_error: 48.6438
Epoch 194/400
1819/1819 [==============================] - 1s 380us/sample - loss: 22.1786 - mean_squared_error: 22.1786 - val_loss: 50.1247 - val_mean_squared_error: 50.1247
Epoch 195/400
1819/1819 [==============================] - 1s 383us/sample - loss: 22.6229 - mean_squared_error: 22.6229 - val_loss: 47.5830 - val_mean_squared_error: 47.5830
Epoch 196/400
1819/1819 [==============================] - 1s 388us/sample - loss: 22.1774 - mean_squared_error: 22.1775 - val_loss: 47.8100 - val_mean_squared_error: 47.8100
Epoch 197/400
1819/1819 [==============================] - 1s 392us/sample - loss: 22.0897 - mean_squared_error: 22.0897 - val_loss: 50.0922 - val_mean_squared_error: 50.0922
Epoch 198/400
1819/1819 [==============================] - 1s 396us/sample - loss: 22.4138 - mean_squared_error: 22.4138 - va

Epoch 240/400
1819/1819 [==============================] - 1s 417us/sample - loss: 19.8665 - mean_squared_error: 19.8665 - val_loss: 46.2712 - val_mean_squared_error: 46.2712
Epoch 241/400
1819/1819 [==============================] - 1s 401us/sample - loss: 20.2064 - mean_squared_error: 20.2064 - val_loss: 46.2471 - val_mean_squared_error: 46.2471
Epoch 242/400
1819/1819 [==============================] - 1s 390us/sample - loss: 19.4838 - mean_squared_error: 19.4838 - val_loss: 47.3725 - val_mean_squared_error: 47.3725
Epoch 243/400
1819/1819 [==============================] - 1s 424us/sample - loss: 19.3450 - mean_squared_error: 19.3450 - val_loss: 47.3983 - val_mean_squared_error: 47.3983
Epoch 244/400
1819/1819 [==============================] - 1s 417us/sample - loss: 19.6242 - mean_squared_error: 19.6242 - val_loss: 47.0168 - val_mean_squared_error: 47.0168
Epoch 245/400
1819/1819 [==============================] - 1s 449us/sample - loss: 19.2651 - mean_squared_error: 19.2651 - va

Epoch 287/400
1819/1819 [==============================] - 1s 381us/sample - loss: 17.5170 - mean_squared_error: 17.5170 - val_loss: 47.2405 - val_mean_squared_error: 47.2406
Epoch 288/400
1819/1819 [==============================] - 1s 390us/sample - loss: 17.2968 - mean_squared_error: 17.2968 - val_loss: 45.1931 - val_mean_squared_error: 45.1931
Epoch 289/400
1819/1819 [==============================] - 1s 392us/sample - loss: 17.2011 - mean_squared_error: 17.2011 - val_loss: 46.1515 - val_mean_squared_error: 46.1515
Epoch 290/400
1819/1819 [==============================] - 1s 388us/sample - loss: 17.5248 - mean_squared_error: 17.5248 - val_loss: 45.3598 - val_mean_squared_error: 45.3598
Epoch 291/400
1819/1819 [==============================] - 1s 391us/sample - loss: 17.5126 - mean_squared_error: 17.5126 - val_loss: 45.2855 - val_mean_squared_error: 45.2855
Epoch 292/400
1819/1819 [==============================] - 1s 433us/sample - loss: 17.2939 - mean_squared_error: 17.2939 - va

Epoch 334/400
1819/1819 [==============================] - 1s 388us/sample - loss: 15.7219 - mean_squared_error: 15.7219 - val_loss: 44.8357 - val_mean_squared_error: 44.8357
Epoch 335/400
1819/1819 [==============================] - 1s 387us/sample - loss: 15.6343 - mean_squared_error: 15.6343 - val_loss: 44.9842 - val_mean_squared_error: 44.9842
Epoch 336/400
1819/1819 [==============================] - 1s 395us/sample - loss: 15.6561 - mean_squared_error: 15.6561 - val_loss: 44.3436 - val_mean_squared_error: 44.3436
Epoch 337/400
1819/1819 [==============================] - 1s 380us/sample - loss: 15.5805 - mean_squared_error: 15.5805 - val_loss: 45.2164 - val_mean_squared_error: 45.2164
Epoch 338/400
1819/1819 [==============================] - 1s 378us/sample - loss: 15.7085 - mean_squared_error: 15.7085 - val_loss: 44.7559 - val_mean_squared_error: 44.7559
Epoch 339/400
1819/1819 [==============================] - 1s 380us/sample - loss: 15.3214 - mean_squared_error: 15.3214 - va

Epoch 381/400
1819/1819 [==============================] - 1s 394us/sample - loss: 14.0706 - mean_squared_error: 14.0706 - val_loss: 43.8524 - val_mean_squared_error: 43.8524
Epoch 382/400
1819/1819 [==============================] - 1s 394us/sample - loss: 13.9782 - mean_squared_error: 13.9782 - val_loss: 43.9866 - val_mean_squared_error: 43.9866
Epoch 383/400
1819/1819 [==============================] - 1s 386us/sample - loss: 14.3473 - mean_squared_error: 14.3473 - val_loss: 44.9630 - val_mean_squared_error: 44.9630
Epoch 384/400
1819/1819 [==============================] - 1s 395us/sample - loss: 14.1879 - mean_squared_error: 14.1879 - val_loss: 45.2958 - val_mean_squared_error: 45.2958
Epoch 385/400
1819/1819 [==============================] - 1s 393us/sample - loss: 13.9932 - mean_squared_error: 13.9932 - val_loss: 43.6219 - val_mean_squared_error: 43.6219
Epoch 386/400
1819/1819 [==============================] - 1s 381us/sample - loss: 13.9755 - mean_squared_error: 13.9755 - va

## Build a two-layer model

Our simple two layer models starts with 200 hidden units in the first layer and then we do a sensitivity to different second layer sizes.

In [25]:
opt_list = {'adam':adam, 'sgd':sgd}
def relu_2l_model(hidden_units, activation):
    relu_2l_model = models.Sequential()
    relu_2l_model.add(layers.Dense(200,activation=activation, kernel_initializer='normal',input_shape=[9216]))
    relu_2l_model.add(layers.Dense(hidden_units,activation=activation))
    relu_2l_model.add(layers.Dense(30, activation='linear'))
    relu_2l_model.build()
    print(relu_2l_model.summary())
    return relu_2l_model

In [26]:
two_layer_df = pd.DataFrame()
for hidden_unit in [50, 100, 150]:
    for act in ['relu']:
        for opt_name, opt in opt_list.items():
            model = relu_2l_model(hidden_units=hidden_unit, activation=act)
            model.compile(optimizer=opt,
                          loss='mean_squared_error',
                          metrics=['mean_squared_error'])
            time_callback = TimeHistory()
            
            # Change epochs to 200 to reduce runtime
            history = model.fit(X, y, epochs=300, validation_split=0.15, callbacks=[time_callback])
            times = time_callback.times

            # Convert to dataframe
            hist = pd.DataFrame(history.history)
            hist['epoch'] = history.epoch
            hist['RMSE'] = np.sqrt(hist.mean_squared_error)
            hist['val_RMSE'] = np.sqrt(hist.val_mean_squared_error)
            hist['times'] = times
            hist['hunits'] = hidden_unit
            hist['activation'] = act
            hist['optimizer'] = opt_name
            hist['lrate'] = opt.get_config()['learning_rate']

            # Keep concatenating to dataframe
            two_layer_df = pd.concat([two_layer_df,hist])
            
            # Re-pickle after every model to retain progress
            two_layer_df.to_pickle("OutputData/two_layer_df.pkl")

            # Save models.
            filename = "two_layer_relu_{}_{}_{}".format(hidden_unit, act, opt_name)
            model.save("Models/"+filename+".h5")

Model: "sequential_60"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_132 (Dense)            (None, 200)               1843400   
_________________________________________________________________
dense_133 (Dense)            (None, 50)                10050     
_________________________________________________________________
dense_134 (Dense)            (None, 30)                1530      
Total params: 1,854,980
Trainable params: 1,854,980
Non-trainable params: 0
_________________________________________________________________
None
Train on 1819 samples, validate on 321 samples
Epoch 1/300
1819/1819 [==============================] - 1s 444us/sample - loss: 317.5782 - mean_squared_error: 317.5783 - val_loss: 182.2151 - val_mean_squared_error: 182.2151
Epoch 2/300
1819/1819 [==============================] - 1s 277us/sample - loss: 146.8479 - mean_squared_error: 146.8479 - val_loss: 132.1824 - 

KeyboardInterrupt: 

KeyboardInterrupt: 